# Summarizing (w/ GPT-2)

## Packages

In [1]:
from utils.json_utils import read_json, write_json
from datasets import Dataset
import pandas as pd

/home/pauli/.local/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Tokenizing

In [2]:
sentences_w_subjects_tokenized = read_json("9_non_lemmatized_tokenized_sentences_black_clover.json")
sentences_w_subjects_tokenized

[{'subjects': ['Yuno'],
  'tokens': ['a',
   'priest',
   'takes',
   'two',
   'babies',
   'abandoned',
   'outside',
   'his',
   'church',
   'inside',
   'and',
   'discovers',
   'two',
   'babies',
   'abandoned',
   'outside',
   'his',
   'church',
   'names',
   'to',
   'be',
   'Yuno',
   'and',
   'Asta',
   '.']},
 {'subjects': ['Asta'],
  'tokens': ['a',
   'priest',
   'takes',
   'two',
   'babies',
   'abandoned',
   'outside',
   'his',
   'church',
   'inside',
   'and',
   'discovers',
   'two',
   'babies',
   'abandoned',
   'outside',
   'his',
   'church',
   'names',
   'to',
   'be',
   'Yuno',
   'and',
   'Asta',
   '.']},
 {'subjects': ['Lily'],
  'tokens': ['Fifteen',
   'years',
   'later',
   ',',
   'Asta',
   'proposes',
   'to',
   'Sister',
   'Lily',
   ',',
   'who',
   'refuses',
   'repeatedly',
   '.']},
 {'subjects': ['Asta'],
  'tokens': ['Fifteen',
   'years',
   'later',
   ',',
   'Asta',
   'proposes',
   'to',
   'Sister',
   'Lily',
   

In [3]:
sentences_w_subjects_tokenized = [
    {
        "subjects" : sentence["subjects"],
        "tokens"  : " ".join(sentence["tokens"])
    } 
    for sentence in sentences_w_subjects_tokenized
]
sentences_w_subjects_tokenized

[{'subjects': ['Yuno'],
  'tokens': 'a priest takes two babies abandoned outside his church inside and discovers two babies abandoned outside his church names to be Yuno and Asta .'},
 {'subjects': ['Asta'],
  'tokens': 'a priest takes two babies abandoned outside his church inside and discovers two babies abandoned outside his church names to be Yuno and Asta .'},
 {'subjects': ['Lily'],
  'tokens': 'Fifteen years later , Asta proposes to Sister Lily , who refuses repeatedly .'},
 {'subjects': ['Asta'],
  'tokens': 'Fifteen years later , Asta proposes to Sister Lily , who refuses repeatedly .'},
 {'subjects': ['Yuno'],
  'tokens': 'Yuno and the other orphans criticize Asta and point out Yuno lack of magic .'},
 {'subjects': ['Asta'],
  'tokens': 'Yuno and the other orphans criticize Asta and point out Yuno lack of magic .'},
 {'subjects': ['Yuno'],
  'tokens': 'Asta tries to show off Asta skills , but Yuno outshines Asta with Asta magic .'},
 {'subjects': ['Asta'],
  'tokens': 'Asta t

In [4]:
max_length = 0
for sentence in sentences_w_subjects_tokenized:
    if len(sentence["tokens"]) > max_length:
        max_length = len(sentence["tokens"])
max_length

610

In [5]:
varied_set_adjectives = read_json("14_varied_set_adjectives_definitions.json")
#varied_set_adjectives

In [6]:
training_sents = []
for adj in varied_set_adjectives:
    training_sents.append("[MASK] can be described as " + adj + ".")
    training_sents.append("[MASK] can be described as " + adj + ".")
    training_sents.append("[MASK] can be described as " + adj + ".")
    training_sents.append("[MASK] can be described as " + adj + ".")
    training_sents.append("[MASK] can be described as " + adj + ".")

training_sents.extend(list(map(lambda x : x["tokens"], sentences_w_subjects_tokenized)))
#training_sents

## Transformer

In [7]:
from transformers import AutoTokenizer, AutoModelForMaskedLM, DataCollatorForLanguageModeling, Trainer, TrainingArguments
import torch

2023-01-26 21:30:23.579465: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-01-26 21:30:23.802136: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-01-26 21:30:23.802149: I tensorflow/compiler/xla/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2023-01-26 21:30:24.475778: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2023-

In [8]:
model_checkpoint = "bert-base-cased"

In [9]:
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint, use_fast=True)

In [10]:
data_collator = DataCollatorForLanguageModeling(tokenizer, mlm=False)

In [11]:
tokenize_fn = lambda doc : tokenizer(
        doc,
        truncation=True,
        max_length=1024
    )

tokenized_dataset = list(map(tokenize_fn, training_sents))

In [12]:
tokenized_dataset = pd.DataFrame(tokenized_dataset)
tokenized_dataset = Dataset.from_pandas(tokenized_dataset)

In [13]:
model = AutoModelForMaskedLM.from_pretrained(
    model_checkpoint, pad_token_id=tokenizer.eos_token_id)

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [14]:
device = f"cuda:{torch.cuda.current_device()}" if torch.cuda.is_available() else "cpu"

In [15]:
training_args = TrainingArguments(
    f"{model_checkpoint}-finetuned-adjs-wsent-black-clover",
    num_train_epochs=2,
    per_device_train_batch_size=10,
    per_device_eval_batch_size=10,    
    learning_rate=2e-5,
    weight_decay=0.01,
    do_eval=True, # eval en validation set
    evaluation_strategy="steps", # eval en validation set
    eval_steps=100,
    save_steps=100, # checkpoint model every 500 steps
    logging_dir='./logs', # logging
    logging_strategy="steps",
    logging_steps=1,
    fp16=False, # float16 en training (only on CUDA)
    push_to_hub=False,
)

In [16]:
trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=tokenized_dataset, #.select(range(0, 128)),
    eval_dataset=tokenized_dataset, #.select(range(0, 128)),
)

In [17]:
train_output = trainer.train()

/home/pauli/.local/lib/python3.10/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 6239
  Num Epochs = 2
  Instantaneous batch size per device = 10
  Total train batch size (w. parallel, distributed & accumulation) = 10
  Gradient Accumulation steps = 1
  Total optimization steps = 1248
  0%|          | 1/1248 [00:01<37:07,  1.79s/it]

{'loss': 1.866, 'learning_rate': 1.998397435897436e-05, 'epoch': 0.0}


  0%|          | 2/1248 [00:03<40:12,  1.94s/it]

{'loss': 1.3938, 'learning_rate': 1.996794871794872e-05, 'epoch': 0.0}


  0%|          | 3/1248 [00:06<46:36,  2.25s/it]

...

{'loss': 0.0002, 'learning_rate': 4.8076923076923085e-08, 'epoch': 2.0}


100%|█████████▉| 1246/1248 [1:45:09<00:04,  2.20s/it]

{'loss': 0.0001, 'learning_rate': 3.205128205128205e-08, 'epoch': 2.0}


100%|█████████▉| 1247/1248 [1:45:11<00:02,  2.37s/it]

{'loss': 0.0, 'learning_rate': 1.6025641025641026e-08, 'epoch': 2.0}


## Summarize

In [ ]:
import numpy as np

In [ ]:
def predict_mask(input_str):
    """Tomamos el camino largo en lugar de usar pipeline
    """
    inputs = tokenizer(input_str, return_tensors="pt")
    mask_index = np.where(inputs['input_ids'] == tokenizer.mask_token_id)
    # .eval() to set dropout and batch normalization layers to evaluation mode
    model.eval()
    outputs = model(**inputs)
    top_5_predictions = torch.softmax(outputs.logits[mask_index], dim=1).topk(5)
    predicted = []
    for i in range(5):
        token = tokenizer.decode(top_5_predictions.indices[0, i])
        prob = top_5_predictions.values[0, i]
        predicted.append({
            "token": token, 
            "prob": prob.item()
        })
    return predicted

In [ ]:
predicted_by_sentence_by_character = []
for sentence in sentences_w_subjects_tokenized:
    predicted_by_character = dict()
    for subject in sentence["subjects"]:
        print(sentence["tokens"] + " " + subject + " can be described as [MASK].")
        print()
        predicted = predict_mask(sentence["tokens"] + " " + subject + " can be described as [MASK].")
        predicted_by_character[subject] = predicted
        for i in range(0, len(predicted)):
            print(f" {i+1}) {predicted[i]['token']:<20} {predicted[i]['prob']:.3f}")
        print()
    predicted_by_sentence_by_character.append(predicted_by_character)

write_json(predicted_by_sentence_by_character, "29_sent_predicted_by_char_bert_sent_coref.json")

a priest takes two babies abandoned outside his church inside and discovers two babies abandoned outside his church names to be Yuno and Asta . Yuno can be described as [MASK].

 1) well                 0.059
 2) dead                 0.018
 3) dangerous            0.017
 4) drunk                0.015
 5) normal               0.011

a priest takes two babies abandoned outside his church inside and discovers two babies abandoned outside his church names to be Yuno and Asta . Asta can be described as [MASK].

 1) well                 0.114
 2) [CLS]                0.023
 3) dangerous            0.016
 4) dead                 0.013
 5) normal               0.011

Fifteen years later , Asta proposes to Sister Lily , who refuses repeatedly . Lily can be described as [MASK].

 1) well                 0.035
 2) dead                 0.024
 3) dangerous            0.015
 4) drunk                0.014
 5) beautiful            0.012

Fifteen years later , Asta proposes to Sister Lily , who refuses

In [ ]:
predicted_by_sentence_by_character

[{'Yuno': [{'token': 'well', 'prob': 0.05913417786359787},
   {'token': 'dead', 'prob': 0.017927514389157295},
   {'token': 'dangerous', 'prob': 0.017457064241170883},
   {'token': 'drunk', 'prob': 0.015289518050849438},
   {'token': 'normal', 'prob': 0.010806072503328323}]},
 {'Asta': [{'token': 'well', 'prob': 0.11448170989751816},
   {'token': '[CLS]', 'prob': 0.022511247545480728},
   {'token': 'dangerous', 'prob': 0.01573476754128933},
   {'token': 'dead', 'prob': 0.012670634314417839},
   {'token': 'normal', 'prob': 0.010935131460428238}]},
 {'Lily': [{'token': 'well', 'prob': 0.03503146022558212},
   {'token': 'dead', 'prob': 0.02427370846271515},
   {'token': 'dangerous', 'prob': 0.015339055098593235},
   {'token': 'drunk', 'prob': 0.014185435138642788},
   {'token': 'beautiful', 'prob': 0.01214889157563448}]},
 {'Asta': [{'token': 'well', 'prob': 0.040930043905973434},
   {'token': 'drunk', 'prob': 0.024186421185731888},
   {'token': 'dead', 'prob': 0.016790080815553665},
   {

In [ ]:
predicted_by_sentence_by_character = []
for sentence in sentences_w_subjects_tokenized:
    predicted_by_character = dict()
    for subject in sentence["subjects"]:
        print(subject + " can be described as [MASK].")
        print()
        predicted = predict_mask(subject + " can be described as [MASK].")
        predicted_by_character[subject] = predicted
        for i in range(0, len(predicted)):
            print(f" {i+1}) {predicted[i]['token']:<20} {predicted[i]['prob']:.3f}")
        print()
    predicted_by_sentence_by_character.append(predicted_by_character)

write_json(predicted_by_sentence_by_character, "29_predicted_by_char_bert_sent_coref.json")

Yuno can be described as [MASK].

 1) well                 0.161
 2) follows              0.023
 3) [CLS]                0.023
 4) drunk                0.009
 5) dangerous            0.008

Asta can be described as [MASK].

 1) well                 0.283
 2) follows              0.052
 3) [CLS]                0.025
 4) ##tral               0.017
 5) ##tern               0.016

Lily can be described as [MASK].

 1) well                 0.216
 2) [CLS]                0.026
 3) normal               0.011
 4) wet                  0.010
 5) dry                  0.010

Asta can be described as [MASK].

 1) well                 0.283
 2) follows              0.052
 3) [CLS]                0.025
 4) ##tral               0.017
 5) ##tern               0.016

Yuno can be described as [MASK].

 1) well                 0.161
 2) follows              0.023
 3) [CLS]                0.023
 4) drunk                0.009
 5) dangerous            0.008

Asta can be described as [MASK].

 1) well        

In [ ]:
predicted_by_sentence_by_character

[{'Yuno': [{'token': 'well', 'prob': 0.16093774139881134},
   {'token': 'follows', 'prob': 0.023116296157240868},
   {'token': '[CLS]', 'prob': 0.022737780585885048},
   {'token': 'drunk', 'prob': 0.008910329081118107},
   {'token': 'dangerous', 'prob': 0.0075854710303246975}]},
 {'Asta': [{'token': 'well', 'prob': 0.2825336158275604},
   {'token': 'follows', 'prob': 0.052406907081604004},
   {'token': '[CLS]', 'prob': 0.024985894560813904},
   {'token': '##tral', 'prob': 0.017321910709142685},
   {'token': '##tern', 'prob': 0.015691304579377174}]},
 {'Lily': [{'token': 'well', 'prob': 0.216403990983963},
   {'token': '[CLS]', 'prob': 0.02634630911052227},
   {'token': 'normal', 'prob': 0.011455900967121124},
   {'token': 'wet', 'prob': 0.010365892201662064},
   {'token': 'dry', 'prob': 0.010297978296875954}]},
 {'Asta': [{'token': 'well', 'prob': 0.2825336158275604},
   {'token': 'follows', 'prob': 0.052406907081604004},
   {'token': '[CLS]', 'prob': 0.024985894560813904},
   {'token'

In [ ]:
def predict_mask_x(input_str, x):
    """Tomamos el camino largo en lugar de usar pipeline
    """
    inputs = tokenizer(input_str, return_tensors="pt")
    mask_index = np.where(inputs['input_ids'] == tokenizer.mask_token_id)
    # .eval() to set dropout and batch normalization layers to evaluation mode
    model.eval()
    outputs = model(**inputs)
    top_x_predictions = torch.softmax(outputs.logits[mask_index], dim=1).topk(x)
    predicted = []
    for i in range(x):
        token = tokenizer.decode(top_x_predictions.indices[0, i])
        prob = top_x_predictions.values[0, i]
        predicted.append({
            "token": token, 
            "prob": prob.item()
        })
    return predicted

In [ ]:
subject = "Asta"
predicted = predict_mask_x(subject + " can be described as [MASK].", 27)
predicted_by_character[subject] = predicted
for i in range(0, len(predicted)):
    print(f" {i+1}) {predicted[i]['token']:<20} {predicted[i]['prob']:.3f}")
print()

 1) well                 0.283
 2) follows              0.052
 3) [CLS]                0.025
 4) ##tral               0.017
 5) ##tern               0.016
 6) such                 0.011
 7) distinct             0.008
 8) ##self               0.007
 9) desired              0.007
 10) normal               0.006
 11) unnecessary          0.005
 12) usual                0.004
 13) necessary            0.004
 14) dangerous            0.004
 15) opposed              0.004
 16) ##tro                0.004
 17) useless              0.004
 18) [MASK]               0.004
 19) ##piration           0.004
 20) impossible           0.003
 21) above                0.003
 22) possible             0.003
 23) dry                  0.003
 24) wet                  0.003
 25) nothing              0.003
 26) sound                0.003
 27) drunk                0.003



In [ ]:
subject = "Asta"
predicted = predict_mask_x(subject + " is [MASK].", 100)
predicted_by_character[subject] = predicted
for i in range(0, len(predicted)):
    print(f" {i+1}) {predicted[i]['token']:<20} {predicted[i]['prob']:.3f}")
print()

 1) blind                0.075
 2) dead                 0.059
 3) destroyed            0.025
 4) killed               0.020
 5) lost                 0.020
 6) defeated             0.017
 7) drunk                0.015
 8) broken               0.014
 9) gone                 0.011
 10) paralyzed            0.009
 11) frozen               0.009
 12) confused             0.008
 13) absent               0.008
 14) missing              0.007
 15) wounded              0.007
 16) exhausted            0.007
 17) weak                 0.006
 18) forgotten            0.006
 19) alive                0.005
 20) hungry               0.005
 21) trapped              0.005
 22) closed               0.005
 23) crushed              0.005
 24) deserted             0.005
 25) buried               0.005
 26) depressed            0.005
 27) silent               0.004
 28) wet                  0.004
 29) angry                0.004
 30) stuck                0.004
 31) abandoned            0.004
 32) imprisoned  

In [ ]:
characters = read_json('3_characters_black_clover.json')
adjectives = read_json("14_varied_set_adjectives.json")

In [ ]:

perplex_adjs = dict()
for character in characters:
    perplex_adjs[character] = dict()
    for adj in adjectives:
        sent = character + " is " + adj
        tokenized_sent = tokenizer(sent)
        tokenized_sent = Dataset.from_list([tokenized_sent])
        perplexity = np.exp(trainer.evaluate(tokenized_sent)["eval_loss"])
        perplex_adjs[character][adj] = perplexity

***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 184.18it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1244.60it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1514.74it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1345.19it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1370.24it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1449.81it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1225.33it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1482.61it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|

In [ ]:
sorted_perplex_adjs = sorted(perplex_adjs["Asta"].items(), key=lambda kv: kv[1])
print(sorted_perplex_adjs)
write_json(sorted_perplex_adjs, "29_asta.json")

[('absent-minded', 1.0000053643578393), ('lanky', 1.0000067437517843), ('flamboyant', 1.0000069140349117), ('charismatic', 1.0000069289420879), ('kind-hearted', 1.000007763456901), ('morose', 1.0000079869133234), ('reclusive', 1.0000081401953396), ('stern', 1.0000082054921358), ('warm-hearted', 1.0000082551773308), ('rotund', 1.000008259410154), ('crestfallen', 1.000008359427208), ('ardent', 1.0000084488794923), ('boisterous', 1.0000089141419124), ('fussy', 1.000009074713737), ('demure', 1.0000095195953873), ('fervent', 1.000009745219549), ('restless', 1.0000098743745207), ('naive', 1.0000098744154484), ('jovial', 1.0000101922597509), ('generous', 1.000010231966876), ('petulant', 1.0000103710536956), ('fastidious', 1.000010535010929), ('zealous', 1.0000105499413512), ('haughty', 1.0000106265188875), ('nosy', 1.00001076280085), ('diligent', 1.0000110693330144), ('venal', 1.0000111374203629), ('drowsy', 1.0000116227850098), ('timid', 1.0000116525503893), ('cantankerous', 1.00001284795939

In [ ]:
sorted_perplex_adjs = sorted(perplex_adjs["Noelle"].items(), key=lambda kv: kv[1])
print(sorted_perplex_adjs)
write_json(sorted_perplex_adjs, "29_noelle.json")

[('absent-minded', 1.0000086681068807), ('lanky', 1.0000103710827997), ('drowsy', 1.0000105414020155), ('charismatic', 1.0000107627135377), ('crestfallen', 1.0000109330692002), ('flamboyant', 1.0000114140999563), ('boisterous', 1.0000119953120723), ('morose', 1.000012142135393), ('petulant', 1.0000129084633993), ('fussy', 1.0000132150626153), ('reclusive', 1.0000135698084986), ('ardent', 1.0000138791937385), ('grouchy', 1.000014049546294), ('shrewd', 1.0000141411164207), ('tetchy', 1.0000148840197547), ('timid', 1.0000149009129609), ('stern', 1.0000155447276855), ('naughty', 1.0000155963423134), ('cantankerous', 1.0000157354662595), ('haughty', 1.0000161724599694), ('warm-hearted', 1.0000161952759228), ('rotund', 1.0000162122582832), ('kind-hearted', 1.0000169105325856), ('obnoxious', 1.0000178960218062), ('venal', 1.0000179407806615), ('nosy', 1.0000186957896906), ('jovial', 1.0000192775299177), ('zealous', 1.0000196182805534), ('fervent', 1.0000197031635438), ('fastidious', 1.0000197

In [ ]:
sorted_perplex_adjs = sorted(perplex_adjs["Yuno"].items(), key=lambda kv: kv[1])
print(sorted_perplex_adjs)
write_json(sorted_perplex_adjs, "29_yuno.json")

[('absent-minded', 1.0000051259507428), ('charismatic', 1.0000064670293722), ('flamboyant', 1.0000069405364067), ('lanky', 1.0000072376299594), ('reclusive', 1.00000793586207), ('ardent', 1.0000080018555313), ('stern', 1.0000081260343918), ('boisterous', 1.0000085962452652), ('warm-hearted', 1.000008821426291), ('petulant', 1.000009029981654), ('kind-hearted', 1.0000090747573929), ('restless', 1.0000094571779927), ('morose', 1.0000095664329924), ('crestfallen', 1.0000099836213805), ('fussy', 1.000010117792297), ('shrewd', 1.0000103049109192), ('generous', 1.0000103313383795), ('demure', 1.000011035245686), ('haughty', 1.0000111374267293), ('fastidious', 1.0000112353704), ('nosy', 1.0000113077688133), ('diligent', 1.0000113418188614), ('timid', 1.000011488625715), ('cantankerous', 1.00001196054804), ('fervent', 1.0000120399542467), ('jovial', 1.0000120399706178), ('venal', 1.000012125160378), ('zealous', 1.0000125168918483), ('grouchy', 1.000012725442525), ('naughty', 1.0000134534916496

In [ ]:
sorted_perplex_adjs = sorted(perplex_adjs["Julius"].items(), key=lambda kv: kv[1])
print(sorted_perplex_adjs)
write_json(sorted_perplex_adjs, "29_julius.json")

[('absent-minded', 1.0000070332782294), ('lanky', 1.000009059820626), ('charismatic', 1.0000096558153528), ('flamboyant', 1.0000101922461084), ('ardent', 1.0000102859586735), ('drowsy', 1.0000112396223355), ('boisterous', 1.0000116973126032), ('warm-hearted', 1.0000121081626254), ('crestfallen', 1.0000121421053794), ('morose', 1.00001222729151), ('reclusive', 1.0000126956298194), ('petulant', 1.0000130276796917), ('haughty', 1.0000134506321599), ('naughty', 1.000013629482167), ('shrewd', 1.0000142304791808), ('timid', 1.0000143219438211), ('fussy', 1.0000147306675824), ('grouchy', 1.0000151564602562), ('kind-hearted', 1.0000153267657348), ('diligent', 1.0000153778746648), ('nosy', 1.0000155765550383), ('cantankerous', 1.0000157056380024), ('rotund', 1.0000162718347916), ('jovial', 1.0000163995390288), ('tetchy', 1.0000166380597735), ('fastidious', 1.0000171659394204), ('demure', 1.0000172850907356), ('zealous', 1.0000176939357635), ('generous', 1.0000180957286087), ('fervent', 1.000018

In [ ]:
sorted_perplex_adjs = sorted(perplex_adjs["Mereleona"].items(), key=lambda kv: kv[1])
print(sorted_perplex_adjs)
write_json(sorted_perplex_adjs, "29_mereleona.json")

[('absent-minded', 1.0000049709816128), ('charismatic', 1.0000071167049496), ('flamboyant', 1.00000713079858), ('lanky', 1.0000071657257), ('reclusive', 1.0000072319528523), ('stern', 1.0000073909032203), ('kind-hearted', 1.0000074862935533), ('boisterous', 1.0000077810548507), ('warm-hearted', 1.0000078319914991), ('restless', 1.0000081657678106), ('morose', 1.0000084756661567), ('fussy', 1.000008559141201), ('haughty', 1.0000085962134326), ('crestfallen', 1.000008809453597), ('naive', 1.0000089853387044), ('petulant', 1.0000090717151056), ('generous', 1.0000091939004683), ('ardent', 1.0000097035488253), ('shrewd', 1.000009764233631), ('zealous', 1.0000099419861173), ('nosy', 1.0000099737387125), ('diligent', 1.0000100664644456), ('demure', 1.000010225367515), ('fastidious', 1.0000102399732398), ('chic', 1.0000102916057843), ('naughty', 1.0000104373383591), ('clumsy', 1.000010520125982), ('jovial', 1.000010549895876), ('funny', 1.0000108181105483), ('cantankerous', 1.000010891278372),

In [ ]:
sorted_perplex_adjs = sorted(perplex_adjs["Charmy"].items(), key=lambda kv: kv[1])
print(sorted_perplex_adjs)
write_json(sorted_perplex_adjs, "29_charmy.json")

[('absent-minded', 1.000004940510206), ('flamboyant', 1.0000075100774728), ('lanky', 1.000007599500122), ('charismatic', 1.0000077352550707), ('reclusive', 1.0000080912341138), ('crestfallen', 1.0000084372615088), ('kind-hearted', 1.000008569771466), ('stern', 1.0000088384230779), ('diligent', 1.0000096558580995), ('morose', 1.000009722040851), ('boisterous', 1.0000097989248267), ('ardent', 1.000009814788389), ('haughty', 1.0000099091266572), ('warm-hearted', 1.0000103578658859), ('restless', 1.0000103710827997), ('petulant', 1.0000105697385315), ('naughty', 1.0000106691091588), ('fervent', 1.000011390914853), ('nosy', 1.000011592979613), ('generous', 1.0000119036957573), ('zealous', 1.0000121857380089), ('fastidious', 1.0000122121809805), ('demure', 1.00001233796837), ('cantankerous', 1.0000123380320356), ('timid', 1.000012463788518), ('fussy', 1.0000124770727632), ('shrewd', 1.000012540691804), ('obnoxious', 1.0000126121489727), ('venal', 1.0000129489546268), ('drowsy', 1.00001352343

In [ ]:
more_similar_vocab = read_json("14_more_similar_vocabulary.json")

In [ ]:
perplex_adjs_simpler = dict()
for character in characters:
    perplex_adjs_simpler[character] = dict()
    for adj in more_similar_vocab:
        sent = character + " is " + adj
        tokenized_sent = tokenizer(sent)
        tokenized_sent = Dataset.from_list([tokenized_sent])
        perplexity = np.exp(trainer.evaluate(tokenized_sent)["eval_loss"])
        perplex_adjs_simpler[character][adj] = perplexity

***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1242.39it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1500.65it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1405.13it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1326.47it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1569.14it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1527.42it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 1558.06it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|██████████| 1/1 [00:00<00:00, 810.49it/s]
***** Running Evaluation *****
  Num examples = 1
  Batch size = 10
100%|

In [ ]:
sorted_perplex_adjs = sorted(perplex_adjs_simpler["Asta"].items(), key=lambda kv: kv[1])
print(sorted_perplex_adjs)
write_json(sorted_perplex_adjs, "29_asta_simpler.json")